# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [30 EVs per week test]

Installing required packages and dependencies

In [61]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [63]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [64]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [65]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [66]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f41655eae50>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 30
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 30, 'EVs_n_max': 1566, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [67]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [68]:
env.plot_ELVIS_data()

In [69]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  31388.25 , over-consume=kWh  47147.39 , under-consume=kWh  15759.14 , Total_cost=€  1174.02 , overcost=€  1649.03 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [70]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [71]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [72]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [73]:
env.plot_VPP_Elvis_comparison()

In [74]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [75]:
env.plot_rewards_stats()

In [76]:
env.plot_EVs_kpi()

In [77]:
env.plot_actions_kpi()

In [78]:
env.plot_load_kpi()

In [79]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [80]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [81]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [82]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  32013.64 , over-consume=kWh  46930.6 , under-consume=kWh  14916.96 , Total_cost=€  1198.21 , overcost=€  1642.92 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -1144.95 , over-consume=KWh  1647.46 , under-consume=KWh  2792.41 , Total_cost=€  -2.24 , Overcost=€  58.15 
 EV_INFO: Av.EV_energy_leaving=kWh  62.87 , Std.EV_energy_leaving=kWh  24.11 , EV_departures =  1566 , EV_queue_left =  0
SCORE:  Cumulative_reward= 472665.22 - Step_rewars (load_t= 433475.38, EVs_energy_t= 5424.04)
 - Final_rewards (EVs_energy= 20787.29, Overconsume= -616.5, Underconsume= 320.08, Overcost= 13274.93)
Episode:1 Score:472665.2231642567


In [83]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [84]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  61.616226  33.324467  45.146717  49.685608   
2022-01-01 00:15:00  61.866226  32.761417  44.583668  49.935608   
2022-01-01 00:30:00  62.116226  32.280041  44.102291  50.185608   
2022-01-01 00:45:00  62.366226  31.878708  43.700958  50.435608   
2022-01-01 01:00:00  62.616226  31.508873  43.331123  50.685608   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  84.368225  41.147778  67.738106  82.626373   
2022-06-06 05:00:00  85.357544  40.897778  68.727425  83.615692   
2022-06-06 05:15:00  86.024475  41.564709  69.394356  84.282623   
2022-06-06 05:30:00  86.786041  42.326275  70.155922  85.044189   
2022-06-06 05:45:00  87.538437  43.078671  70.908318  85.796585   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [20343, 20345, 20342, 20344]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [20343, 20345, 20342, 20344]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [20343, 20345, 20342, 20344]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [20343, 20345, 20342, 20344]  [1, 2, 2, 1]   
...                                           ...           ...   
2022-06-06 04:45:00  [21025, 21028, 21026, 21027]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [21025, 21028, 21026, 21027]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [21025, 21028, 21026, 21027]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [21025, 21028, 21026, 21027]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [21025, 21028, 21026, 21027]  [1, 1, 1, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.157562e+00         15.0   
2022-01-01 00:15:00    [False, True, True, False]  0.000000e+00         15.0   
2022-01-01 00:30:00    [False, True, True, False]  0.000000e+00         15.0   
2022-01-01 00:45:00    [False, True, True, False]  0.000000e+00         15.0   
2022-01-01 01:00:00    [False, True, True, False] -1.110223e-16         15.0   
...                                           ...           ...          ...   
2022-06-06 04:45:00     [True, False, True, True]  0.000000e+00         15.0   
2022-06-06 05:00:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:15:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:30:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:45:00      [True, True, True, True]  0.000000e+00         15.0   

                     EV_reward  rewards  
time                                     
2022-01-01 00:00:00        0.0     15.0  
2022-01-01 00:15:00        0.0     15.0  
2022-01-01 00:30:00        0.0     15.0  
2022-01-01 00:45:00        0.0     15.0  
2022-01-01 01:00:00        0.0     15.0  
...                        ...      ...  
2022-06-06 04:45:00        0.0     15.0  
2022-06-06 05:00:00        0.0     15.0  
2022-06-06 05:15:00        0.0     15.0  
2022-06-06 05:30:00        0.0     15.0  
2022-06-06 05:45:00        0.0     15.0  

[15000 rows x 11 columns]

In [85]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [86]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [87]:
env.plot_VPP_Elvis_comparison()

In [88]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [89]:
env.plot_rewards_stats()

In [90]:
env.plot_EVs_kpi()

In [91]:
env.plot_load_kpi()

In [92]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [93]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 21911, Arrival time: 2022-01-01 13:00:00, Parking_time: 24, Leaving_time: 2022-01-02 13:00:00, SOC: 0.439344444458569, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 23475, Arrival time: 2022-12-31 17:30:00, Parking_time: 24, Leaving_time: 2023-01-01 17:30:00, SOC: 0.4654836856230621, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  23748.16 , over-consume=kWh  42966.69 , under-consume=kWh  19218.53 , Total_cost=€  1087.04 , overcost=€  1863.36 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59


In [94]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [95]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [96]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22907.06 , over-consume=kWh  42159.3 , under-consume=kWh  19252.24 , Total_cost=€  1037.87 , overcost=€  1831.05 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3453.83 , over-consume=KWh  810.58 , under-consume=KWh  4264.41 , Total_cost=€  -119.74 , Overcost=€  35.06 
 EV_INFO: Av.EV_energy_leaving=kWh  66.8 , Std.EV_energy_leaving=kWh  23.52 , EV_departures =  1562 , EV_queue_left =  0
SCORE:  Cumulative_reward= 487688.16 - Step_rewars (load_t= 420932.96, EVs_energy_t= 27386.68)
 - Final_rewards (EVs_energy= 22635.86, Overconsume= 773.33, Underconsume= -403.16, Overcost= 16362.5)
Episode:1 Score:487688.1629849431


In [97]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [98]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  92.802795  29.578457  74.429146  69.355896   
2022-06-06 05:00:00  94.025101  29.328457  75.651451  70.578201   
2022-06-06 05:15:00  95.321594  29.078457  76.947945  71.874695   
2022-06-06 05:30:00  96.474403  28.828457  78.100754  73.027504   
2022-06-06 05:45:00  97.639297  28.578457  79.265648  74.192398   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 04:45:00  [25700, 25702, 25701, 25703]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [25700, 25702, 25701, 25703]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [25700, 25702, 25701, 25703]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [25700, 25702, 25701, 25703]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [25700, 25702, 25701, 25703]  [1, 2, 1, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, False, False, True] -3.282733e+00    -5.366624   
2022-01-01 00:15:00  [False, False, False, True] -4.403286e+00    -4.726897   
2022-01-01 00:30:00  [False, False, False, True] -3.836138e+00    -3.931284   
2022-01-01 00:45:00  [False, False, False, True] -3.358770e+00    -5.214262   
2022-01-01 01:00:00   [False, True, False, True] -4.235688e+00    -5.218803   
...                                          ...           ...          ...   
2022-06-06 04:45:00   [False, False, True, True]  0.000000e+00    15.000000   
2022-06-06 05:00:00   [False, False, True, True]  1.776357e-15    15.000000   
2022-06-06 05:15:00   [False, False, True, True]  0.000000e+00    15.000000   
2022-06-06 05:30:00   [False, False, True, True]  0.000000e+00    15.000000   
2022-06-06 05:45:00   [False, False, True, True]  0.000000e+00    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.366624  
2022-01-01 00:15:00        0.0  -4.726897  
2022-01-01 00:30:00        0.0  -3.931284  
2022-01-01 00:45:00        0.0  -5.214262  
2022-01-01 01:00:00        0.0  -5.218803  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [99]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [100]:
env.plot_VPP_Elvis_comparison()

In [101]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [102]:
env.plot_rewards_stats()

In [103]:
env.plot_EVs_kpi()

In [104]:
env.plot_load_kpi()

In [105]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [106]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 26606, Arrival time: 2022-01-01 07:00:00, Parking_time: 24, Leaving_time: 2022-01-02 07:00:00, SOC: 0.41734903427781334, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 28170, Arrival time: 2022-12-31 21:30:00, Parking_time: 24, Leaving_time: 2023-01-01 21:30:00, SOC: 0.6123156921128823, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18754.29 , over-consume=kWh  40454.77 , under-consume=kWh  21700.48 , Total_cost=€  875.92 , overcost=€  1678.87 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79


In [107]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [108]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [109]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18074.59 , over-consume=kWh  39242.62 , under-consume=kWh  21168.03 , Total_cost=€  843.62 , overcost=€  1627.71 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4180.53 , over-consume=KWh  652.74 , under-consume=KWh  4833.27 , Total_cost=€  -143.97 , Overcost=€  26.38 
 EV_INFO: Av.EV_energy_leaving=kWh  69.21 , Std.EV_energy_leaving=kWh  23.3 , EV_departures =  1561 , EV_queue_left =  0
SCORE:  Cumulative_reward= 496736.67 - Step_rewars (load_t= 416389.36, EVs_energy_t= 36880.0)
 - Final_rewards (EVs_energy= 23711.39, Overconsume= 3366.53, Underconsume= -531.17, Overcost= 16920.56)
Episode:1 Score:496736.6744681596


In [110]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [111]:
VPP_table.head(14995)

0         1          2          3  \
time                                                             
2022-01-01 00:00:00   0.000000   0.00000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.00000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.00000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.00000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.00000   0.000000   0.000000   
...                        ...       ...        ...        ...   
2022-06-06 03:30:00  63.941254  51.33136  50.642292  38.106365   
2022-06-06 03:45:00  64.708656  51.08136  50.392292  38.873768   
2022-06-06 04:00:00  65.728592  50.83136  50.142292  39.893703   
2022-06-06 04:15:00  66.333664  50.58136  50.747364  40.498775   
2022-06-06 04:30:00  67.053360  50.33136  51.467056  41.218468   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [30410, 30411, 30412, 30413]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [30410, 30411, 30412, 30413]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [30410, 30411, 30412, 30413]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [30410, 30411, 30412, 30413]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [30410, 30411, 30412, 30413]  [1, 2, 1, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, False, False, True] -4.037867e+00    -3.138855   
2022-01-01 00:15:00  [False, False, False, True] -2.883313e+00    -3.876996   
2022-01-01 00:30:00  [False, False, False, True] -3.326198e+00    -3.965146   
2022-01-01 00:45:00  [False, False, False, True] -3.379088e+00    -5.526831   
2022-01-01 01:00:00   [False, True, False, True] -4.579514e+00    -6.092736   
...                                          ...           ...          ...   
2022-06-06 03:30:00   [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 03:45:00   [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 04:00:00    [True, False, True, True]  8.881784e-16    15.000000   
2022-06-06 04:15:00    [True, False, True, True]  0.000000e+00    15.000000   
2022-06-06 04:30:00    [True, False, True, True]  8.881784e-16    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -3.138855  
2022-01-01 00:15:00        0.0  -3.876996  
2022-01-01 00:30:00        0.0  -3.965146  
2022-01-01 00:45:00        0.0  -5.526831  
2022-01-01 01:00:00        0.0  -6.092736  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [112]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [113]:
env.plot_VPP_Elvis_comparison()

In [114]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [115]:
env.plot_rewards_stats()

In [116]:
env.plot_EVs_kpi()

In [117]:
env.plot_actions_kpi()

In [118]:
env.plot_load_kpi()

In [119]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [120]:
#env.close()